In [7]:
import pandas as pd
from tqdm.notebook import tqdm

In [8]:
df = pd.read_csv('/Users/ormeiri/Desktop/Homework/predictive models/predictive models/data/training_v2.csv')
df

encounter_id  patient_id  hospital_id  hospital_death   age        bmi  \
0             66154       25312          118               0  68.0  22.730000   
1            114252       59342           81               0  77.0  27.420000   
2            119783       50777          118               0  25.0  31.950000   
3             79267       46918          118               0  81.0  22.640000   
4             92056       34377           33               0  19.0        NaN   
...             ...         ...          ...             ...   ...        ...   
91708         91592       78108           30               0  75.0  23.060250   
91709         66119       13486          121               0  56.0  47.179671   
91710          8981       58179          195               0  48.0  27.236914   
91711         33776      120598           66               0   NaN  23.297481   
91712          1671       53612          104               0  82.0  22.031250   

       elective_surgery  ethnicity gender  height  ... aids cirrhosis  \
0                     0  Caucasian      M   180.3  ...  0.0       0.0   
1                     0  Caucasian      F   160.0  ...  0.0       0.0   
2                     0  Caucasian      F   172.7  ...  0.0       0.0   
3                     1  Caucasian      F   165.1  ...  0.0       0.0   
4                     0  Caucasian      M   188.0  ...  0.0       0.0   
...                 ...        ...    ...     ...  ...  ...       ...   
91708                 0  Caucasian      M   177.8  ...  0.0       0.0   
91709                 0  Caucasian      F   183.0  ...  0.0       0.0   
91710                 0  Caucasian      M   170.2  ...  0.0       0.0   
91711                 0  Caucasian      F   154.9  ...  0.0       0.0   
91712                 1  Caucasian      F   160.0  ...  0.0       0.0   

       diabetes_mellitus hepatic_failure immunosuppression  leukemia  \
0                    1.0             0.0               0.0       0.0   
1                    1.0             0.0               0.0       0.0   
2                    0.0             0.0               0.0       0.0   
3                    0.0             0.0               0.0       0.0   
4                    0.0             0.0               0.0       0.0   
...                  ...             ...               ...       ...   
91708                1.0             0.0               0.0       0.0   
91709                0.0             0.0               0.0       0.0   
91710                1.0             0.0               0.0       0.0   
91711                0.0             0.0               0.0       0.0   
91712                0.0             0.0               0.0       0.0   

       lymphoma  solid_tumor_with_metastasis  apache_3j_bodysystem  \
0           0.0                          0.0                Sepsis   
1           0.0                          0.0           Respiratory   
2           0.0                          0.0             Metabolic   
3           0.0                          0.0        Cardiovascular   
4           0.0                          0.0                Trauma   
...         ...                          ...                   ...   
91708       0.0                          1.0                Sepsis   
91709       0.0                          0.0                Sepsis   
91710       0.0                          0.0             Metabolic   
91711       0.0                          0.0           Respiratory   
91712       0.0                          0.0      Gastrointestinal   

       apache_2_bodysystem  
0           Cardiovascular  
1              Respiratory  
2                Metabolic  
3           Cardiovascular  
4                   Trauma  
...                    ...  
91708       Cardiovascular  
91709       Cardiovascular  
91710            Metabolic  
91711          Respiratory  
91712     Gastrointestinal  

[91713 rows x 186 columns]

In [12]:
def drop_columns(df, columns_to_drop):
    """
    Drop specified columns from a DataFrame.
    
    Parameters:
    df (pandas.DataFrame): The input DataFrame
    columns_to_drop (list): List of column names to drop
    
    Returns:
    pandas.DataFrame: DataFrame with specified columns removed
    """
    # Make a copy to avoid modifying the original DataFrame
    df_copy = df.copy()
    
    # Check which columns actually exist in the DataFrame
    existing_columns = [col for col in columns_to_drop if col in df.columns]
    
    if len(existing_columns) < len(columns_to_drop):
        missing_columns = set(columns_to_drop) - set(existing_columns)
        print(f"Warning: These columns don't exist in the DataFrame: {missing_columns}")
    
    if not existing_columns:
        print("No columns to drop")
        return df_copy
        
    # Drop the columns
    df_copy = df_copy.drop(columns=existing_columns)
    
    print(f"Dropped {len(existing_columns)} columns")
    return df_copy
    

In [13]:
df.columns

Index(['encounter_id', 'patient_id', 'hospital_id', 'hospital_death', 'age',
       'bmi', 'elective_surgery', 'ethnicity', 'gender', 'height',
       ...
       'aids', 'cirrhosis', 'diabetes_mellitus', 'hepatic_failure',
       'immunosuppression', 'leukemia', 'lymphoma',
       'solid_tumor_with_metastasis', 'apache_3j_bodysystem',
       'apache_2_bodysystem'],
      dtype='object', length=186)

In [14]:
columns_to_drop = ['encounter_id', 'patient_id']
df = drop_columns(df, columns_to_drop)
df.columns

Dropped 2 columns


Index(['hospital_id', 'hospital_death', 'age', 'bmi', 'elective_surgery',
       'ethnicity', 'gender', 'height', 'hospital_admit_source',
       'icu_admit_source',
       ...
       'aids', 'cirrhosis', 'diabetes_mellitus', 'hepatic_failure',
       'immunosuppression', 'leukemia', 'lymphoma',
       'solid_tumor_with_metastasis', 'apache_3j_bodysystem',
       'apache_2_bodysystem'],
      dtype='object', length=184)

In [9]:
def convert_tabular_to_text(data_df, target_column='hospital_death', output_file='text_data.csv'):
    """
    Convert tabular data to text using the Text Template approach from TabLLM paper
    and save the result to a CSV file. Shows progress with tqdm.
    
    Parameters:
    data_df (pandas.DataFrame): The input tabular data
    target_column (str): The name of the column to predict/exclude from text generation
    output_file (str): Path to save the output CSV file
    
    Returns:
    dict: Dictionary with two keys:
          'texts': List of text descriptions for each row
          'labels': List of corresponding target values
    """
    texts = []
    labels = []
    
    # Get all columns except the target column
    feature_columns = [col for col in data_df.columns if col != target_column]
    
    # Iterate through each row with progress bar
    for _, row in tqdm(data_df.iterrows(), total=len(data_df), desc="Converting rows to text"):
        # Convert each row to sentences
        sentences = []
        for column in feature_columns:
            # Handling missing values
            if pd.isna(row[column]):
                value = "N/A"
            else:
                value = row[column]
            
            # Create sentence for this feature
            sentence = f"The {column} is {value}."
            sentences.append(sentence)
        
        # Join all sentences into a single text
        text = " ".join(sentences)
        texts.append(text)
        
        # Store the target value
        labels.append(row[target_column])
    
    # Create a DataFrame with the text data and labels
    result_df = pd.DataFrame({
        'text': texts,
        'label': labels
    })
    
    # Save to CSV
    result_df.to_csv(output_file, index=False)
    print(f"Results saved to {output_file}")
    
    return {
        'texts': texts,
        'labels': labels
    }

In [10]:
result = convert_tabular_to_text(df)

Converting rows to text:   0%|          | 0/91713 [00:00<?, ?it/s]

Results saved to text_data.csv


In [11]:
result

{'texts': ['The encounter_id is 66154. The patient_id is 25312. The hospital_id is 118. The age is 68.0. The bmi is 22.73. The elective_surgery is 0. The ethnicity is Caucasian. The gender is M. The height is 180.3. The hospital_admit_source is Floor. The icu_admit_source is Floor. The icu_id is 92. The icu_stay_type is admit. The icu_type is CTICU. The pre_icu_los_days is 0.541666667. The readmission_status is 0. The weight is 73.9. The albumin_apache is 2.3. The apache_2_diagnosis is 113.0. The apache_3j_diagnosis is 502.01. The apache_post_operative is 0. The arf_apache is 0.0. The bilirubin_apache is 0.4. The bun_apache is 31.0. The creatinine_apache is 2.51. The fio2_apache is N/A. The gcs_eyes_apache is 3.0. The gcs_motor_apache is 6.0. The gcs_unable_apache is 0.0. The gcs_verbal_apache is 4.0. The glucose_apache is 168.0. The heart_rate_apache is 118.0. The hematocrit_apache is 27.4. The intubated_apache is 0.0. The map_apache is 40.0. The paco2_apache is N/A. The paco2_for_ph_